### 安装必备的包

In [1]:
import subprocess
print(subprocess.getoutput("pip install gast==0.2.2"))
print(subprocess.getoutput("pip install FER"))

Defaulting to user installation because normal site-packages is not writeable
Processing /usr4/cs640/johnyin/.cache/pip/wheels/21/7f/02/420f32a803f7d0967b48dd823da3f558c5166991bfd204eef3/gast-0.2.2-py3-none-any.whl
ERROR: tensorflow 2.3.1 has requirement gast==0.3.3, but you'll have gast 0.2.2 which is incompatible.
ERROR: tensorflow 2.3.1 has requirement keras-preprocessing<1.2,>=1.1.1, but you'll have keras-preprocessing 1.1.0 which is incompatible.
ERROR: tensorflow 2.3.1 has requirement tensorboard<3,>=2.3.0, but you'll have tensorboard 2.1.1 which is incompatible.
ERROR: tensorflow 2.3.1 has requirement tensorflow-estimator<2.4.0,>=2.3.0, but you'll have tensorflow-estimator 2.1.0 which is incompatible.
You should consider upgrading via the '/share/pkg.7/python3/3.7.7/install/bin/python3.7 -m pip install --upgrade pip' command.
Defaulting to user installation because normal site-packages is not writeable
  Using cached tensorflow_estimator-2.3.0-py2.py3-none-any.whl (459 kB)
  Usi

### 数据地址遍历器

In [1]:
import os

BASE_PATH = os.path.abspath(os.path.join('.', 'data'))
NAME = "2020"
OUT = "output_" + NAME
DIR = os.path.join(BASE_PATH, NAME)

### 以下是数据加载程序

In [2]:
# 数据加载程序
import os
import pandas as pd

class DataLoader:
    def __init__(self, dir):
        video_path = os.path.join(dir, "VideoClips")
        csv_file = os.path.join(dir, "Labels.csv")
        data = pd.read_csv(csv_file)
        self.filenames = list(map(lambda x: os.path.join(video_path, x), list(data["Filename"])))
        self.labels = list(data["Label"])

    def __len__(self):
        return len(self.labels)
        
    def __getitem__(self, item):
        assert(0 <= item < len(self.labels))
        return self.filenames[item], self.labels[item]

    def __iter__(self):
        for dat in zip(self.filenames, self.labels):
            yield dat

In [3]:
from fer import FER, Video
import cv2

Instructions for updating:
non-resource variables are not supported in the long term


In [32]:
import json
import re
import ipdb

import numpy

class MyEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, numpy.integer):
            return int(obj)
        elif isinstance(obj, numpy.floating):
            return float(obj)
        elif isinstance(obj, numpy.ndarray):
            return obj.tolist()
        else:
            return super(MyEncoder, self).default(obj)

def analyze(detector, data_dir: str, output: str):
    import shutil
    assert(len(output) > 0)
    dl = DataLoader(data_dir)
    
    # 创建用于保存输出文件的文件夹
    out = os.path.abspath(os.path.join(".", output))
    
    t_out = os.path.join(output, "run")
    v_out = os.path.join(output, "video")
    p_warn = os.path.join(output, "warn.txt")
    p_log = os.path.join(output, "log.txt")
    
    if os.path.exists(p_warn):
        os.remove(p_warn)
    if os.path.exists(t_out):
        shutil.rmtree(t_out)
    if os.path.exists(v_out):
        shutil.rmtree(v_out)
    os.makedirs(t_out)
    
    line_num = -1
    if os.path.exists(p_log) and os.path.isfile(p_log):
        with open(p_log, "r", encoding="utf-8") as log_read:
            line = log_read.read()
        re_ans = re.findall(r"(\d+)", line)
        if len(re_ans) == 1:
            line_num = int(re_ans[0])
            print("读取到上一次运行正常的行数: '{0:d}'\n跳过 {0:d} 行文件。".format(line_num))
    f_warn = open(p_warn, "w", encoding="utf-8")
    idx = 0
    for video_path, _ in dl:
        if line_num >= 0:
            if idx <= line_num:
                idx += 1
                continue
        print("==================\nLine {0:d}".format(idx))
        _, name = os.path.split(video_path)
        name, ext = os.path.splitext(name)
        
        video = Video(video_path)
        video.outdir = v_out
        try:
            raw_data = video.analyze(detector, display=False)
        except IndexError:
            f_warn.write("视频 '{0:s}.{1:s}' 中没有检测到任何脸！\n".format(name, ext))
            f_warn.flush()
            raw_data = []
            
        with open(os.path.join(t_out, name + ".txt"), "w", encoding="utf-8") as f:
            json.dump(raw_data, f, cls=MyEncoder)
        
        with open(p_log, "w", encoding="utf-8") as log_write:
            log_write.write("{0:d}".format(idx))
        idx += 1
    if os.path.exists(p_log):
        os.remove(p_log)
        
    f_warn.close()

In [5]:
detector = FER(mtcnn=False)

Instructions for updating:
If using Keras pass *_constraint arguments to layers.


02-12-2020:01:36:20,199 WARNING  [deprecation.py:506] From /share/pkg.7/tensorflow/2.1.0/install/lib/SCC/../python3.7-gpu/site-packages/tensorflow_core/python/ops/resource_variable_ops.py:1635: calling BaseResourceVariable.__init__ (from tensorflow.python.ops.resource_variable_ops) with constraint is deprecated and will be removed in a future version.
Instructions for updating:
If using Keras pass *_constraint arguments to layers.


02-12-2020:01:36:20,807 WARNING  [backend.py:558] OMP_NUM_THREADS is no longer used by the default Keras config. To configure the number of threads, use tf.config.threading APIs.


In [31]:
analyze(detector, DIR, OUT)

02-12-2020:01:59:11,387 INFO     [classes.py:211] 59.94 fps, 60 frames, 1.00 seconds
02-12-2020:01:59:11,389 INFO     [classes.py:218] Making directories at output_2020/video


读取到上一次运行正常的行数: '1'
跳过 1 行文件。
Line 2
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Startin

02-12-2020:01:59:13,59 INFO     [classes.py:328] Completed analysis: saved to output_2020/video/biden_138_0_output.mp4
02-12-2020:01:59:13,88 INFO     [classes.py:211] 59.94 fps, 123 frames, 2.05 seconds
02-12-2020:01:59:13,89 INFO     [classes.py:218] Making directories at output_2020/video


Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Line 3
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Sta

02-12-2020:01:59:18,922 INFO     [classes.py:328] Completed analysis: saved to output_2020/video/biden_139_2_output.mp4


...

02-12-2020:04:50:00,950 INFO     [classes.py:328] Completed analysis: saved to output_2020/video/yang_574_0_output.mp4
02-12-2020:04:50:01,8 INFO     [classes.py:211] 29.97 fps, 30 frames, 1.00 seconds
02-12-2020:04:50:01,9 INFO     [classes.py:218] Making directories at output_2020/video


Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Line 1505
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished
Starting to Zip
Zip has finished


02-12-2020:04:50:02,664 INFO     [classes.py:328] Completed analysis: saved to output_2020/video/yang_886_0_output.mp4


Starting to Zip
Zip has finished
Starting to Zip
Zip has finished


NameError: name 'f_log' is not defined